In [1]:
import torch

# Humandoid MARL
from Humanoid_MARL import envs
from Humanoid_MARL.envs.base_env import GymWrapper, VectorGymWrapper
from Humanoid_MARL.utils.torch_utils import save_models, load_models
from Humanoid_MARL.agent.ppo.train_torch import eval_unroll, get_agent_actions
from Humanoid_MARL.agent.ppo.agent import Agent
from Humanoid_MARL.envs.torch_wrapper import TorchWrapper
from IPython.display import HTML
from brax.io import html
import jax
from Humanoid_MARL import envs
from Humanoid_MARL.utils.utils import load_reward_config
from Humanoid_MARL import CONFIG_REWARD

In [2]:

config = {
        'num_timesteps': 100_000_000,
        'eval_frequency': 10,
        'episode_length': 1000,
        'unroll_length': 10,
        'num_minibatches': 32,
        'num_update_epochs': 8,
        'discounting': 0.97,
        'learning_rate': 3e-4,
        'entropy_cost': 1e-3,
        'num_envs': 2048,
        'batch_size': 512,
        'env_name': "humanoid",
        'render' : False,
        'device' : 'cuda',
        'model_path' : "../models/20240227_115117_ppo_humanoid_standing_dim_246.pt",
        'video_length' : 300,
    }
env_config = load_reward_config(CONFIG_REWARD, config['env_name'])
env = envs.create(
        config['env_name'], batch_size=None, episode_length=config['episode_length'], backend="generalized", **env_config
    )
env = GymWrapper(env, get_jax_state=True)
env = TorchWrapper(env, device=config['device'], get_jax_state=True)

# env warmup
observation = env.reset()
action = torch.zeros(env.action_space.shape[0] * env.num_agents).to(config['device'])
env.step(action)
jax_states = []
num_steps = 1000
agents = load_models(config['model_path'], Agent, device=config['device'])

Models loaded from ../models/20240227_115117_ppo_humanoid_standing_dim_246.pt


In [3]:
eval_reward = 0.0
episodes = torch.zeros((), device = config['device'])
for i in range(num_steps):
    print(f"{i} / {num_steps}")
    logits, action = get_agent_actions(agents, observation, env.obs_dims)
    jax_state, observation, reward, done, info = env.step(Agent.dist_postprocess(action[0]))
    episodes += torch.sum(done)
    jax_states.append(jax_state)
    print(f"{i} | {info} | DONE [{done}] | Reward [{reward}]")
    eval_reward += reward
print(f"Total Reward | {eval_reward / episodes}")

0 / 1000
0 | {'distance_from_origin': tensor(0.9340, device='cuda:0'), 'first_obs': tensor([ 1.3927e+00,  9.8043e-01, -1.0096e-02, -8.3504e-03,  1.6423e-02,
        -6.0150e-03, -4.7392e-04,  1.0036e-02, -4.3838e-03,  1.7474e-02,
        -1.5846e-02,  6.6491e-03, -1.2142e-02,  1.6133e-02,  1.4735e-02,
        -1.9016e-02, -2.5006e-03,  1.6019e-02,  1.1542e-02, -3.7860e-03,
         5.8756e-03, -1.0876e-02, -2.0215e-04,  9.7298e-03, -9.4376e-03,
         5.5671e-03,  4.9754e-03,  3.9325e-03, -2.3958e-03, -3.3779e-03,
        -8.9924e-03, -1.6078e-02,  1.6519e-02,  9.3890e-03, -1.7726e-02,
         1.2122e-02, -3.5083e-04, -1.0926e-02, -5.3731e-03,  1.7128e-02,
        -1.9181e-02,  1.1466e-02, -2.4417e-03,  1.4796e-03,  1.6517e-02,
         2.1758e+00,  1.9003e-03,  1.0589e-01,  1.9003e-03,  2.1620e+00,
        -2.6434e-02,  1.0589e-01, -2.6434e-02,  4.7198e-02,  8.9075e+00,
         9.0931e-02,  1.4645e-04,  1.1752e-02,  1.4645e-04,  8.6540e-02,
         2.6579e-04,  1.1752e-02,  2.657

In [4]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

In [5]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

: 